In [3]:
import numpy as np
import gurobipy as grb
import csv
import time
import statsmodels.api as sm
from joblib import Parallel,delayed

def five_variate(n,SNR,rho):
    beta1 = np.array([1,1,1,0,1])
    beta2 = np.array([-1,-1,-1,0,-1])
    p = len(beta1)
    Sigma = np.zeros((p,p));
    for i in range(p):
        for j in range(p):
            Sigma[i,j] = rho**(abs(i-j))
    X = np.random.multivariate_normal(mean =np.zeros(p), cov = Sigma, size = n)
    noise1 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta1)/SNR), size = int(n/2)) 
    noise2 = np.random.normal(0,np.sqrt(np.var(X[:int(n/2)]@beta2)/SNR), size = int(n/2)) 
    Y1 = X[:int(n/2)]@beta1 + noise1
    Y2 = X[int(n/2):]@beta2 + noise2
    Y = np.r_[Y1,Y2]
    lam = 0.1*n
    ols = sm.OLS(Y, X)
    ols_result = ols.fit()
    bigM = 10*float(1.96*(sum(ols_result.bse)))#1000

    M = grb.Model()
    M.Params.TimeLimit = 400
    beta = M.addMVar((int(n),5), lb = -grb.GRB.INFINITY)
    z = M.addMVar(len(Y) - 1, vtype = grb.GRB.BINARY)
    sum_of_sq = sum((Y[t] - sum(X[t,j]*beta[t,j] for j in range(5)))* (Y[t] - sum(X[t,j]*beta[t,j] for j in range(5))) for t in range(len(Y)))
    for t in range(len(Y)-1):
        for j in range(5):
            M.addConstr((beta[t+1,j] - beta[t,j])*(beta[t+1,j] - beta[t,j]) <= bigM*z[t])
            #M.addConstr(beta[t+1,j] - beta[t,j] >= -bigM*z[t])
    #optional constratins to add more cuts
    M.addConstr(sum(z) <= 5)
    for t in range(1, len(Y) - 2):
        M.addConstr(z[t-1] + z[t] + z[t+1] <= 1)
    M.setObjective(sum_of_sq+ lam*sum(z))
    M.optimize()
    beta_hat = [beta[t].x for t in range(len(Y))]
    z_hat = [z[t].x for t in range(len(Y)-1)]
    opt_gap = M.MIPGap
    return z_hat, opt_gap,beta_hat

SNR_list = np.array([6, 3.52, 2.07, 1.22, 0.71])
rho_list = np.array([0, 0.3, 0.7])
n_list = np.array([1000])

header = ['Repitition','Time','rho', 'SNR', 'n', 'Optimality Gap', 'Change Points']#, 'beta_hat', 'nonzero count']
f = open('simulation_five_variate_squared_bigM.csv', 'w')
writer = csv.writer(f)
writer.writerow(header)
f.close()

def to_repeat(rep):
    for n in n_list:
        for SNR in SNR_list:
            for rho in rho_list:
                tik = time.time()
                z_hat, opt_gap, beta_hat = five_variate(n,SNR,rho)
                tok = time.time()
                duration = tok - tik
                cps = [idx for idx,item in enumerate(z_hat) if item == 1 ]
                # Write result
                resultrow = [rep,duration,rho,SNR, n, opt_gap, cps]
                f = open('simulation_five_variate_squared_bigM.csv', 'a')
                writer = csv.writer(f)
                writer.writerow(resultrow)
                f.close()
                
Parallel(n_jobs = 8)(delayed(to_repeat)(rep) for rep in range(500)) #Tomo's machine has 8 cores.

Set parameter Username
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter TimeLimit to value 400
Set parameter Username
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Set parameter Username
Set parameter Username
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter TimeLimit to value 400
Academic license - for non-commercial use only - expires 2024-02-18
Set parameter

   6   4.99547713e+02 -6.85195263e+03  9.49e-04 6.27e-07  1.57e-01     2s
Ordering time: 0.04s
Presolve time: 0.71s
Presolved: 15983 rows, 20984 columns, 38955 nonzeros
Presolved model has 15000 quadratic objective terms
Presolved model has 4995 quadratic constraint(s)
Variable types: 19985 continuous, 999 integer (999 binary)

Barrier statistics:
 Dense cols : 1
 Free vars  : 5000
 AA' NZ     : 2.766e+05
 Factor NZ  : 5.455e+05 (roughly 30 MB of memory)
 Factor Ops : 8.568e+06 (less than 1 second per iteration)
 Threads    : 4
Variable types: 19985 continuous, 999 integer (999 binary)
Root relaxation presolve removed 999 rows and 999 columns
Root relaxation presolve time: 1.00s
Root relaxation presolved: 45955 rows, 20987 columns, 72929 nonzeros
Root relaxation presolved model has 4996 second-order cone constraints

                  Objective                Residual
Iter       Primal          Dual         Primal    Dual     Compl     Time
Root barrier log...

   0   3.78967501e+06 -1

   4   1.22372285e+03 -1.02942810e+04  5.67e+00 1.33e-06  2.50e-01     2s
   3   3.28700788e+03 -1.37388375e+05  2.23e+01 9.81e-06  3.06e+00     2s
   5   6.43087388e+02 -8.23909873e+03  6.51e-01 8.67e-07  1.89e-01     3s
   4   1.22718177e+03 -1.88264017e+04  5.42e+00 1.66e-06  4.29e-01     2s
   6   3.76910519e+02 -4.10291129e+03  3.66e-04 4.74e-07  9.54e-02     3s
  14   2.46190503e+02  2.45533044e+02  5.41e-08 8.28e-07  1.40e-05     4s
   4   1.31567724e+03 -2.23312046e+04  8.33e+00 1.80e-06  5.09e-01     2s
   7   3.23664364e+02 -8.41610035e+02  2.13e-04 1.90e-07  2.48e-02     3s
   5   6.47767421e+02 -3.55400361e+03  6.98e-01 6.75e-07  8.95e-02     2s
   5   6.28374619e+02 -1.09797238e+04  2.38e-02 1.11e-06  2.47e-01     2s
   4   1.36052342e+03 -1.83932888e+04  6.61e+00 1.97e-06  4.24e-01     2s
   6   5.24778614e+02 -5.40226571e+03  3.63e-04 5.45e-07  1.26e-01     3s
  15   2.46146226e+02  2.46046650e+02  1.00e-08 1.71e-06  2.12e-06     4s
   5   6.72824296e+02 -1.17019123e+04 

  16   2.40234331e+02  2.40233957e+02  3.39e-11 5.57e-08  7.96e-09    21s

Barrier solved model in 16 iterations and 20.83 seconds (0.33 work units)
Optimal objective 2.40234331e+02


Root relaxation: objective 2.402343e+02, 0 iterations, 20.00 seconds (0.30 work units)

    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0  240.23433    0  998 4946.96555  240.23433  95.1%     -   22s
H    0     0                    4751.3780282  246.13705  94.8%     -   24s
     0     0  458.53627    0  722 4751.37803  458.53627  90.3%     -   30s
     0     0  226.99240    0  999 4309.54715  226.99240  94.7%     -   30s
H    0     0                    4273.0705878  226.99240  94.7%     -   33s
  13   2.19108754e+02  2.17190365e+02  1.07e-12 1.15e-08  4.09e-05    33s
     0     0  235.02961    0  999 4554.57056  235.02961  94.8%     -   33s
  14   2.18980923e+02  2.18661785e+02  2.75e-13 2.69e

     0     0  422.57011    0    - 4518.15590  422.57011  90.6%     -  177s
     0     0  462.94285    0    - 4266.18824  462.94285  89.1%     -  180s
     0     0  436.75065    0    - 4875.66170  436.75065  91.0%     -  181s
     0     0  456.87742    0    - 4672.30385  456.87742  90.2%     -  182s
     0     2  423.01636    0    1  716.21738  423.01636  40.9%     -  185s
     0     2  458.53627    0    1  793.65459  458.53627  42.2%     -  194s
     0     0  456.48551    0    - 4679.57357  456.48551  90.2%     -  193s
     0     0  462.94285    0    - 4266.18824  462.94285  89.1%     -  193s
     1     2  423.01636    1    1  716.21738  423.01636  40.9%  2922  194s
     0     0  412.86782    0    - 4325.80255  412.86782  90.5%     -  194s
     3     2  423.01636    2    1  716.21738  423.01636  40.9%  2511  199s
     0     0  422.57011    0    - 4518.15590  422.57011  90.6%     -  201s
     0     0  462.94285    0    1 4266.18824  462.94285  89.1%     -  202s
     1     2  458.53627  

...

  1965  1965 5508.12876   71   75 7030.44002 5327.21883  24.2%  25.2  224s
   260   292 5548.49207   59   96 8240.75594 5453.25754  33.8%  19.5  115s
  1966  1966 6071.79780  487   91 7030.44002 5460.06309  22.3%  25.2  229s
   467   503 5611.09957  101   88 8240.75594 5453.25754  33.8%  17.7  120s
  1967  1966 5568.49081  115   88 7030.44002 5568.49081  20.8%  25.1  231s
   615   643 5649.09251  132   91 8240.75594 5453.25754  33.8%  17.5  125s
  1971  1969 5760.64142  245  101 7030.44002 5634.15926  19.9%  25.1  236s
  1976  1972 5903.55507  346  103 7030.44002 5672.35230  19.3%  25.0  240s
   794   839 5704.66140  184   87 8240.75594 5453.25754  33.8%  17.0  130s
  1985  1978 5715.26459  214  105 7030.44002 5715.26459  18.7%  24.9  245s
   918   995 5771.59715  226   81 8240.75594 5453.25754  33.8%  17.2  136s
  1078  1206 5835.38702  279   52 8240.75594 5453.25754  33.8%  16.5  141s
  1987  1980 5724.92108  193  103 7030.44002 5724.92108  18.6%  24.9  255s
  1336  1451 5992.67062  


    Nodes    |    Current Node    |     Objective Bounds      |     Work
 Expl Unexpl |  Obj  Depth IntInf | Incumbent    BestBd   Gap | It/Node Time

     0     0 4353.46433    0  999 24865.0340 4353.46433  82.5%     -    1s
     0     0 4353.46433    0  999 24865.0340 4353.46433  82.5%     -    2s
H    0     0                    24288.700907 4353.46433  82.1%     -    3s
  2029  1707 6882.56587  482  104 8150.46818 6882.56587  15.6%  92.2  325s
     0     0 7678.42157    0  764 24288.7009 7678.42157  68.4%     -    6s
     0     0 7678.42157    0    - 24288.7009 7678.42157  68.4%     -    7s
     0     0 7678.42157    0    - 24288.7009 7678.42157  68.4%     -    8s
  2032  1709 6882.58639  147  104 8150.46818 6882.58639  15.6%  92.1  330s
     0     0 7678.42157    0    1 24288.7009 7678.42157  68.4%     -   11s
H    0     0                    23543.706504 7678.42157  67.4%     -   11s
H    0     0                    23225.821236 7678.42157  66.9%     -   13s
  2033  1713 6894.91578

    27    32 11067.0703    7  168 14106.0519 11039.9252  21.7%   397  124s
H   30    32                    14071.868081 11039.9252  21.5%   359  124s
    31    36 11073.7374    8  168 14071.8681 11039.9252  21.5%   350  125s
    58    66 11100.8972   14  172 14071.8681 11039.9252  21.5%   198  130s
   140   164 11212.6045   31  171 14071.8681 11039.9252  21.5%   102  135s
     0     0 7991.74705    0    1 22193.0543 7991.74705  64.0%     -   32s
H    0     0                    14060.684368 7991.74705  43.2%     -   32s
H    0     0                    14060.593132 7991.74705  43.2%     -   32s
   184   205 11223.6971   36  177 14071.8681 11039.9252  21.5%  82.5  143s
   240   282 11252.4457   50  174 14071.8681 11039.9252  21.5%  67.4  146s
   385   420 11312.3267   90  166 14071.8681 11039.9252  21.5%  48.8  150s
     0     0 7991.74705    0   30 14060.5931 7991.74705  43.2%     -   47s
   549   593 11389.8321  119  166 14071.8681 11039.9252  21.5%  40.9  156s
   673   736 11472.2425  

  2022  1969 11897.8006   33  122 13933.4134 11695.4291  16.1%  96.5  345s
  2039  1978 11699.3973   35  132 13933.4134 11699.3973  16.0%  96.9  352s
  2056  1998 11704.2634   37  138 13933.4134 11704.2634  16.0%  97.2  355s
  2101  2040 11711.8556   41  138 13933.4134 11711.8556  15.9%  98.3  360s
  2177  2090 11723.6618   48  148 13933.4134 11722.3218  15.9%   100  366s
  2231  2130 11736.0122   54  154 13933.4134 11722.3218  15.9%   101  371s
  2291  2169 11751.9883   61  155 13933.4134 11722.3218  15.9%   103  376s
  2359  2222 11971.4458   67  138 13933.4134 11722.3218  15.9%   104  381s
  2440  2283 11779.9350   76  157 13933.4134 11722.3218  15.9%   105  386s
  2519  2336 11910.4585   85  148 13933.4134 11722.3218  15.9%   106  392s
  2613  2405 11827.6879   96  158 13933.4134 11722.3218  15.9%   107  398s
  2663  2420 11835.6682  101  161 13933.4134 11722.3218  15.9%   107  400s

Cutting planes:
  Gomory: 2
  Implied bound: 4026
  MIR: 538
  Flow cover: 131
  Relax-and-lift: 49

[None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None,
 None]